In [3]:
import numpy as np
import pandas as pd
from glob import glob
from matplotlib import pyplot as plt
from matplotlib import patches
import os
from tqdm import tqdm

from scipy.spatial import distance
from scipy.ndimage.filters import maximum_filter
from scipy.ndimage.morphology import generate_binary_structure, iterate_structure, binary_erosion

In [4]:
SCREEN_WIDTH = 640
SCREEN_HEIGHT = 480

HUD_WIDTH = 0
HUD_HEIGHT = 96 # 640 x 384
# HUD_HEIGHT = 104 # 640 x 376

ORIGIN_SHAPE = (128, 128)
KERNEL_SHAPE = (20, 12)
TILE_SIZE = 32

In [17]:
data_dir = "../data_compressed4/36/"

In [18]:
def get_players_vpds(rep_name, data_dir):
    vpd_paths = glob(data_dir + "*.vpd")
    print(vpd_paths)
    dataframes = [pd.read_csv(_, index_col=None )for _ in vpd_paths]
    num_dataset = len(dataframes)
    
    result = []
    for dataframe in dataframes:
        dataframe = dataframe.set_index('frame')
        dataframe = dataframe.reindex(range(dataframe.tail(1).index[0]))
        dataframe = dataframe.fillna(method='ffill')
        dataframe = dataframe.reset_index()
        dataframe = dataframe.astype(int)
        dataframe = dataframe.set_index('frame')
        result.append(dataframe)
        
    print(result)
    dataframes = pd.concat(result, axis=1)
    dataframes = dataframes.fillna(method='ffill')
    dataframes = dataframes.astype(int)
    
    dataframes_columns = []
    for i in range(num_dataset):
        dataframes_columns.append('vpx_{}'.format(i + 1))
        dataframes_columns.append('vpy_{}'.format(i + 1))
    dataframes.columns = dataframes_columns
    
    return dataframes, num_dataset

In [19]:
def mapping_vpd_into_channel(vpds_tile, kernel_shape=KERNEL_SHAPE, origin_shape=ORIGIN_SHAPE, num_dataset=5):
    frames = np.zeros((np.max(vpds_tile.index.max()) + 1,) + (origin_shape))
    kernel = np.ones(kernel_shape)
    
    for idx, row in vpds_tile.iterrows():
        for i in range(num_dataset):
            frames[idx][row['vpx_{}'.format(i+1)]:row['vpx_{}'.format(i+1)] + kernel.shape[0], row['vpy_{}'.format(i+1)]:row['vpy_{}'.format(i+1)] + kernel_shape[1]] += kernel
    return frames     

In [20]:
def kernel_sum(frame, origin_shape=ORIGIN_SHAPE, kernel_shape=KERNEL_SHAPE):
    width_tile = origin_shape[0] - kernel_shape[0]
    height_tile = origin_shape[1] - kernel_shape[1]

    result = np.zeros((width_tile, height_tile))
    
    for x in range(width_tile):
        for y in range(height_tile):
            result[x][y] = frame[x:x+kernel_shape[0],y:y+kernel_shape[1]].sum()
            # print(x, x+kernel_width, y, y+kernel_height, frame[x:x+kernel_width,y:y+kernel_height].sum())
            # print(frame[x:x+kernel_width,y:y+kernel_height].shape)

    max_vpx = np.argmax(result)
    max_vpx_tile = (max_vpx // height_tile) * TILE_SIZE
    max_vpy_tile = (max_vpx % height_tile) * TILE_SIZE
    
    return result, (max_vpx_tile, max_vpy_tile)

In [21]:
def vpds_tile_into_channel_kernel_sum(channel_vpds):
    res_kernel_sum = []
    max_vp_coord = []
    
    for t, frame in tqdm(enumerate(channel_vpds), total=channel_vpds.shape[0]):
        res, coord = kernel_sum(frame, kernel_shape=KERNEL_SHAPE)
        res_kernel_sum.append(res)
        max_vp_coord.append(coord)
    
    return np.asarray(res_kernel_sum), np.asarray(max_vp_coord)

In [22]:
def find_unique_peaks(peaks, threshhold):
    
    tmp = peaks.reshape(peaks.shape[0], 1, peaks.shape[1])
    distance_each = np.sqrt(np.einsum('ijk, ijk->ij', peaks - tmp, peaks - tmp))
    
    tf_mat = distance_each > threshold    
    tf_mat_except_diagonal = tf_mat[~np.eye(tf_mat.shape[0],dtype=bool)].reshape(tf_mat.shape[0], -1)    
    
    all_true = np.bitwise_and.reduce(tf_mat_except_diagonal, axis=1)
    ## 다른 걸로부터 독립적인 것들
    isolated = np.where(all_true)
    ## 서로 독립적이지 않은 것들
    not_isolated = np.where(~all_true)
    
    ## 서로 독립적이지 않은 것들중 Unique한 것을 찾음
    not_isolated_result = []
    not_isolated_unique = np.unique(tf_mat_except_diagonal[~all_true], axis=0)
    for idx in range(not_isolated_unique.shape[0]):
        niche = np.asarray([(tf_mat_except_diagonal[tf_idx] == not_isolated_unique[idx]).all() for tf_idx in range(tf_mat_except_diagonal.shape[0])])
        not_isolated_result.append(peaks[niche].mean(axis=0).astype(int))

    return peaks[isolated], np.asarray(not_isolated_result)

In [23]:
vpds, num_dataset = get_players_vpds("36.rep",data_dir)
vpds_tile = (vpds / TILE_SIZE).astype(int)

['../data_compressed4/36\\36v_1.rep.vpd', '../data_compressed4/36\\36v_2.rep.vpd', '../data_compressed4/36\\36v_3.rep.vpd', '../data_compressed4/36\\36v_4.rep.vpd', '../data_compressed4/36\\36v_5.rep.vpd']
[        vpx   vpy
frame            
0      3456    64
1      3456    64
2      3456    64
3      3456    64
4      3456    64
...     ...   ...
28312  2352  1488
28313  2352  1488
28314  2344  1504
28315  2280  1568
28316  2216  1632

[28317 rows x 2 columns],         vpx   vpy
frame            
0      3456    64
1      3456    64
2      3456    64
3      3456    64
4      3456    64
...     ...   ...
28325  2272  1792
28326  2272  1792
28327  2272  1792
28328  2272  1792
28329  2272  1792

[28330 rows x 2 columns],         vpx   vpy
frame            
0      3456    64
1      3456    64
2      3456    64
3      3456    64
4      3456    64
...     ...   ...
28324  1344  1184
28325  1344  1184
28326  1344  1184
28327  1344  1184
28328  1344  1184

[28329 rows x 2 columns],         vp

In [ ]:
channel_vpds = mapping_vpd_into_channel(vpds_tile)

In [51]:
channel_kernel_sums, max_vpd_coords = vpds_tile_into_channel_kernel_sum(channel_vpds)

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 28253/28253 [19:24<00:00, 24.26it/s]


In [160]:
vpds_label = pd.DataFrame((max_vpd_coords/32).astype(int), columns=['vpx_1', 'vpy_1'])

In [162]:
vpds_label_masked =mapping_vpd_into_channel(vpds_label, num_dataset=1)

In [164]:
vpds_label_masked.shape

(28253, 128, 128)

In [167]:
np.save("../data/vpds_label_masked.npy",vpds_label_masked)

In [165]:
vpds_label_masked

array([[[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       ...,

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0.

In [1]:
vpds_label_masked

NameError: name 'vpds_label_masked' is not defined

In [153]:
dataframe123.index.name="frame"

In [154]:
dataframe123

vpx_1  vpy_1
frame              
0      107.0    2.0
1      107.0    2.0
2      107.0    2.0
3      107.0    2.0
4      107.0    2.0
...      ...    ...
28248   86.0   82.0
28249   86.0   83.0
28250   86.0   83.0
28251   86.0   83.0
28252   86.0   83.0

[28253 rows x 2 columns]

In [158]:
kkkk =mapping_vpd_into_channel(dataframe123, num_dataset=1)

In [159]:
kkkk

array([[[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 1., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.]],

       ...,

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0.

In [116]:
dataframe123.shape
    

(28253, 2)

In [130]:
KERNEL_SHAPE

(20, 12)

In [79]:
num_dataset

5

In [ ]:
def mapping_vpd_into_channel123(vpds_tile, kernel_shape=KERNEL_SHAPE, origin_shape=ORIGIN_SHAPE, num_dataset=5):
    frames = np.zeros((np.max(vpds_tile.index.max()) + 1,) + (origin_shape))
    kernel = np.ones(kernel_shape)
    
    for idx, row in vpds_tile.iterrows():
        for i in range(num_dataset):
            frames[idx][row['vpx_{}'.format(i+1)]:row['vpx_{}'.format(i+1)] + kernel.shape[0], row['vpy_{}'.format(i+1)]:row['vpy_{}'.format(i+1)] + kernel_shape[1]] += kernel
    return frames    

In [92]:
kernel_shape=KERNEL_SHAPE, origin_shape=ORIGIN_SHAPE

In [155]:
for idx, row in dataframe123.iterrows():
    print(row)

vpx_1    107.0
vpy_1      2.0
Name: 0, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 1, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 2, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 3, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 4, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 5, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 6, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 7, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 8, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 9, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 10, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 11, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 12, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 13, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 14, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 15, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 16, dtype: float64
vpx_1    107.0
vpy_1      2.0
Name: 17, dtype: float64
vpx_1    107.0
vpy_1

Name: 436, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 437, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 438, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 439, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 440, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 441, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 442, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 443, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 444, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 445, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 446, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 447, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 448, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 449, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 450, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 451, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 452, dtype: float64
vpx_1    107.0
vpy_1    112.0
Name: 453, dtype: float64
vpx_1    107.0
vpy_1  

Name: 835, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 836, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 837, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 838, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 839, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 840, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 841, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 842, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 843, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 844, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 845, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 846, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 847, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 848, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 849, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 850, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 851, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 852, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 853, dtype: float64
vpx_1    0.0
vpy_1    3.0
Name: 854, d

Name: 1223, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1224, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1225, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1226, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1227, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1228, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1229, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1230, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1231, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1232, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1233, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1234, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1235, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1236, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1237, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1238, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1239, dtype: float64
vpx_1    100.0
vpy_1     87.0
Name: 1240, dtype: float64
vpx_

Name: 1605, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1606, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1607, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1608, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1609, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1610, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1611, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1612, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1613, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1614, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1615, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1616, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1617, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1618, dtype: float64
vpx_1    99.0
vpy_1    51.0
Name: 1619, dtype: float64
vpx_1    101.0
vpy_1     51.0
Name: 1620, dtype: float64
vpx_1    101.0
vpy_1     51.0
Name: 1621, dtype: float64
vpx_1    101.0
vpy_1     51.0
Name: 1622, dtype: float64
vpx_1    101.0
vpy_1     51.0
Na

...

Name: 26420, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26421, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26422, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26423, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26424, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26425, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26426, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26427, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26428, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26429, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26430, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26431, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26432, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26433, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26434, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26435, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26436, dtype: float64
vpx_1    91.0
vpy_1    56.0
Name: 26437, dtype: float64
vpx_1    91.0
vpy_1 

Name: 26773, dtype: float64
vpx_1     25.0
vpy_1    101.0
Name: 26774, dtype: float64
vpx_1     25.0
vpy_1    101.0
Name: 26775, dtype: float64
vpx_1     25.0
vpy_1    101.0
Name: 26776, dtype: float64
vpx_1    11.0
vpy_1    98.0
Name: 26777, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26778, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26779, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26780, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26781, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26782, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26783, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26784, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26785, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26786, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26787, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26788, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26789, dtype: float64
vpx_1    11.0
vpy_1    99.0
Name: 26790, dtype: float64
vpx_1    11.0


Name: 27116, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27117, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27118, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27119, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27120, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27121, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27122, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27123, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27124, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27125, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27126, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27127, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27128, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27129, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27130, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27131, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27132, dtype: float64
vpx_1    45.0
vpy_1    29.0
Name: 27133, dtype: float64
vpx_1    45.0
vpy_1 

Name: 27508, dtype: float64
vpx_1    81.0
vpy_1    74.0
Name: 27509, dtype: float64
vpx_1    81.0
vpy_1    74.0
Name: 27510, dtype: float64
vpx_1    81.0
vpy_1    74.0
Name: 27511, dtype: float64
vpx_1    81.0
vpy_1    74.0
Name: 27512, dtype: float64
vpx_1    81.0
vpy_1    74.0
Name: 27513, dtype: float64
vpx_1    81.0
vpy_1    74.0
Name: 27514, dtype: float64
vpx_1    81.0
vpy_1    74.0
Name: 27515, dtype: float64
vpx_1    81.0
vpy_1    74.0
Name: 27516, dtype: float64
vpx_1    81.0
vpy_1    74.0
Name: 27517, dtype: float64
vpx_1    76.0
vpy_1    75.0
Name: 27518, dtype: float64
vpx_1    77.0
vpy_1    76.0
Name: 27519, dtype: float64
vpx_1    77.0
vpy_1    77.0
Name: 27520, dtype: float64
vpx_1    81.0
vpy_1    79.0
Name: 27521, dtype: float64
vpx_1    81.0
vpy_1    79.0
Name: 27522, dtype: float64
vpx_1    78.0
vpy_1    79.0
Name: 27523, dtype: float64
vpx_1    78.0
vpy_1    79.0
Name: 27524, dtype: float64
vpx_1    80.0
vpy_1    79.0
Name: 27525, dtype: float64
vpx_1    80.0
vpy_1 

Name: 27911, dtype: float64
vpx_1     50.0
vpy_1    108.0
Name: 27912, dtype: float64
vpx_1     50.0
vpy_1    108.0
Name: 27913, dtype: float64
vpx_1     50.0
vpy_1    108.0
Name: 27914, dtype: float64
vpx_1     50.0
vpy_1    108.0
Name: 27915, dtype: float64
vpx_1     50.0
vpy_1    108.0
Name: 27916, dtype: float64
vpx_1     50.0
vpy_1    108.0
Name: 27917, dtype: float64
vpx_1     50.0
vpy_1    108.0
Name: 27918, dtype: float64
vpx_1     50.0
vpy_1    108.0
Name: 27919, dtype: float64
vpx_1     50.0
vpy_1    108.0
Name: 27920, dtype: float64
vpx_1     55.0
vpy_1    108.0
Name: 27921, dtype: float64
vpx_1     55.0
vpy_1    109.0
Name: 27922, dtype: float64
vpx_1     55.0
vpy_1    110.0
Name: 27923, dtype: float64
vpx_1     55.0
vpy_1    111.0
Name: 27924, dtype: float64
vpx_1    83.0
vpy_1    61.0
Name: 27925, dtype: float64
vpx_1    83.0
vpy_1    61.0
Name: 27926, dtype: float64
vpx_1    83.0
vpy_1    61.0
Name: 27927, dtype: float64
vpx_1    83.0
vpy_1    61.0
Name: 27928, dtype: fl

In [93]:
kernel_shape, origin_shape

((128, 128), 128)

In [95]:
num_dataset

5

In [84]:
frames = np.zeros((np.max(vpds_tile.index.max()) + 1,) + (ORIGIN_SHAPE))

In [89]:
kernel = np.ones(KERNEL_SHAPE)

In [121]:
kernel

array([[1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1.,

In [117]:
for idx, row in dataframe123.iterrows():
    for i in range(1):
        frames[idx][row['vpx_{}'.format(i+1)]:row['vpx_{}'.format(i+1)] + kernel.shape[0], row['vpy_{}'.format(i+1)]:row['vpy_{}'.format(i+1)] + kernel_shape[1]] += kernel

ValueError: operands could not be broadcast together with shapes (0,64) (20,12) (0,64) 

In [132]:
for idx, row in dataframe123.iterrows():    
    frames[idx][row['vpx_1'.format(i+1)]:row['vpx_1'.format(i+1)] + kernel.shape[0], row['vpy_1'.format(i+1)]:row['vpy_1'.format(i+1)] + kernel_shape[1]] += kernel

ValueError: operands could not be broadcast together with shapes (0,64) (20,12) (0,64) 

In [141]:
frames.shape

(28253, 128, 128)

In [144]:
for idx, row in dataframe123.iterrows():    
    print(frames[0].shape)
    print(row)
#     print(frames[idx][row['vpx_1']:row['vpx_1'] + kernel.shape[0], row['vpy_1']:row['vpy_1'] + kernel_shape[1]].shape)

(128, 128)
vpx_1    3424
vpy_1      64
Name: 0, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 1, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 2, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 3, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 4, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 5, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 6, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 7, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 8, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 9, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 10, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 11, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 12, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 13, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 14, dtype: int64
(128, 128)
vpx_1    3424
vpy_1      64
Name: 15, dtype: int64
(128, 128)
vpx_1  

Name: 558, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 559, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 560, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 561, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 562, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 563, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 564, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 565, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 566, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 567, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 568, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 569, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 570, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 571, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 572, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 573, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 574, dtype: int64
(128, 128)
vpx_1     0
vpy_1    

Name: 1005, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1006, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1007, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1008, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1009, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1010, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1011, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1012, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1013, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1014, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1015, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1016, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1017, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1018, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1019, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1020, dtype: int64
(128, 128)
vpx_1     0
vpy_1    64
Name: 1021, dtype: int64
(128, 128)
vpx_

vpx_1    3008
vpy_1    1856
Name: 1497, dtype: int64
(128, 128)
vpx_1    3008
vpy_1    1856
Name: 1498, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1499, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1500, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1501, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1502, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1503, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1504, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1505, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1506, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1507, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1508, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1509, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1510, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1511, dtype: int64
(128, 128)
vpx_1    3168
vpy_1    2688
Name: 1512, 

Name: 1979, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1980, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1981, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1982, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1983, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1984, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1985, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1986, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1987, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1988, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1989, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1990, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1991, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1992, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1993, dtype: int64
(128, 128)
vpx_1    2048
vpy_1    1120
Name: 1994, dtype: int64
(128, 128)
vpx_

...

Name: 26399, dtype: int64
(128, 128)
vpx_1       0
vpy_1    2144
Name: 26400, dtype: int64
(128, 128)
vpx_1       0
vpy_1    2144
Name: 26401, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26402, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26403, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26404, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26405, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26406, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26407, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26408, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26409, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26410, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26411, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26412, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26413, dtype: int64
(128, 128)
vpx_1    2912
vpy_1    1792
Name: 26414, dtype: int64

Name: 26871, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26872, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26873, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26874, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26875, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26876, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26877, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26878, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26879, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26880, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26881, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26882, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26883, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26884, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26885, dtype: int64
(128, 128)
vpx_1     288
vpy_1    3168
Name: 26886, dtype: int64

Name: 27317, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1536
Name: 27318, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1536
Name: 27319, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1536
Name: 27320, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1472
Name: 27321, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1472
Name: 27322, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1472
Name: 27323, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1472
Name: 27324, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1472
Name: 27325, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1472
Name: 27326, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1472
Name: 27327, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1472
Name: 27328, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1472
Name: 27329, dtype: int64
(128, 128)
vpx_1    2336
vpy_1    1472
Name: 27330, dtype: int64
(128, 128)
vpx_1    2208
vpy_1    1472
Name: 27331, dtype: int64
(128, 128)
vpx_1    2208
vpy_1    1568
Name: 27332, dtype: int64

Name: 27774, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27775, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27776, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27777, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27778, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27779, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27780, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27781, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27782, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27783, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27784, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27785, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27786, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27787, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27788, dtype: int64
(128, 128)
vpx_1    1824
vpy_1    2272
Name: 27789, dtype: int64

Name: 28221, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28222, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28223, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28224, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28225, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28226, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28227, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28228, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28229, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28230, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28231, dtype: int64
(128, 128)
vpx_1    2656
vpy_1    2592
Name: 28232, dtype: int64
(128, 128)
vpx_1    2752
vpy_1    2592
Name: 28233, dtype: int64
(128, 128)
vpx_1    2752
vpy_1    2624
Name: 28234, dtype: int64
(128, 128)
vpx_1    2752
vpy_1    2624
Name: 28235, dtype: int64
(128, 128)
vpx_1    2752
vpy_1    2624
Name: 28236, dtype: int64

In [134]:
frames.shape

(28253, 128, 128)

In [135]:
dataframe123

vpx_1  vpy_1
frame              
0       3424     64
1       3424     64
2       3424     64
3       3424     64
4       3424     64
...      ...    ...
28248   2752   2624
28249   2752   2656
28250   2752   2656
28251   2752   2656
28252   2752   2656

[28253 rows x 2 columns]

In [136]:
for idx, row in dataframe123.iterrows():
    print(idx)
    print(row)

0
vpx_1    3424
vpy_1      64
Name: 0, dtype: int64
1
vpx_1    3424
vpy_1      64
Name: 1, dtype: int64
2
vpx_1    3424
vpy_1      64
Name: 2, dtype: int64
3
vpx_1    3424
vpy_1      64
Name: 3, dtype: int64
4
vpx_1    3424
vpy_1      64
Name: 4, dtype: int64
5
vpx_1    3424
vpy_1      64
Name: 5, dtype: int64
6
vpx_1    3424
vpy_1      64
Name: 6, dtype: int64
7
vpx_1    3424
vpy_1      64
Name: 7, dtype: int64
8
vpx_1    3424
vpy_1      64
Name: 8, dtype: int64
9
vpx_1    3424
vpy_1      64
Name: 9, dtype: int64
10
vpx_1    3424
vpy_1      64
Name: 10, dtype: int64
11
vpx_1    3424
vpy_1      64
Name: 11, dtype: int64
12
vpx_1    3424
vpy_1      64
Name: 12, dtype: int64
13
vpx_1    3424
vpy_1      64
Name: 13, dtype: int64
14
vpx_1    3424
vpy_1      64
Name: 14, dtype: int64
15
vpx_1    3424
vpy_1      64
Name: 15, dtype: int64
16
vpx_1    3424
vpy_1      64
Name: 16, dtype: int64
17
vpx_1    3424
vpy_1      64
Name: 17, dtype: int64
18
vpx_1    3424
vpy_1      64
Name: 18, dtype: 

Name: 495, dtype: int64
496
vpx_1    32
vpy_1    64
Name: 496, dtype: int64
497
vpx_1    32
vpy_1    64
Name: 497, dtype: int64
498
vpx_1    32
vpy_1    64
Name: 498, dtype: int64
499
vpx_1    32
vpy_1    64
Name: 499, dtype: int64
500
vpx_1    32
vpy_1    64
Name: 500, dtype: int64
501
vpx_1    32
vpy_1    64
Name: 501, dtype: int64
502
vpx_1    32
vpy_1    64
Name: 502, dtype: int64
503
vpx_1    32
vpy_1    64
Name: 503, dtype: int64
504
vpx_1    32
vpy_1    64
Name: 504, dtype: int64
505
vpx_1    32
vpy_1    64
Name: 505, dtype: int64
506
vpx_1    32
vpy_1    64
Name: 506, dtype: int64
507
vpx_1    32
vpy_1    64
Name: 507, dtype: int64
508
vpx_1    32
vpy_1    64
Name: 508, dtype: int64
509
vpx_1    32
vpy_1    64
Name: 509, dtype: int64
510
vpx_1    32
vpy_1    64
Name: 510, dtype: int64
511
vpx_1    32
vpy_1    64
Name: 511, dtype: int64
512
vpx_1    32
vpy_1    64
Name: 512, dtype: int64
513
vpx_1    32
vpy_1    64
Name: 513, dtype: int64
514
vpx_1    32
vpy_1    64
Name: 514, d

934
vpx_1    3424
vpy_1    3552
Name: 934, dtype: int64
935
vpx_1    3424
vpy_1    3552
Name: 935, dtype: int64
936
vpx_1    3424
vpy_1    3552
Name: 936, dtype: int64
937
vpx_1    3424
vpy_1    3552
Name: 937, dtype: int64
938
vpx_1    3424
vpy_1    3552
Name: 938, dtype: int64
939
vpx_1    3424
vpy_1    3552
Name: 939, dtype: int64
940
vpx_1    3424
vpy_1    3552
Name: 940, dtype: int64
941
vpx_1    3424
vpy_1    3552
Name: 941, dtype: int64
942
vpx_1    3424
vpy_1    3552
Name: 942, dtype: int64
943
vpx_1    3424
vpy_1    3552
Name: 943, dtype: int64
944
vpx_1    3424
vpy_1    3552
Name: 944, dtype: int64
945
vpx_1    3424
vpy_1    3552
Name: 945, dtype: int64
946
vpx_1    3424
vpy_1    3552
Name: 946, dtype: int64
947
vpx_1    3424
vpy_1    3552
Name: 947, dtype: int64
948
vpx_1    3424
vpy_1    3552
Name: 948, dtype: int64
949
vpx_1    3424
vpy_1    3552
Name: 949, dtype: int64
950
vpx_1    3424
vpy_1    3552
Name: 950, dtype: int64
951
vpx_1    3424
vpy_1    3552
Name: 951, dtype

1434
vpx_1    2752
vpy_1    2048
Name: 1434, dtype: int64
1435
vpx_1    2752
vpy_1    2048
Name: 1435, dtype: int64
1436
vpx_1    2752
vpy_1    2048
Name: 1436, dtype: int64
1437
vpx_1    2752
vpy_1    2048
Name: 1437, dtype: int64
1438
vpx_1    2752
vpy_1    2048
Name: 1438, dtype: int64
1439
vpx_1    2752
vpy_1    2048
Name: 1439, dtype: int64
1440
vpx_1    2752
vpy_1    2048
Name: 1440, dtype: int64
1441
vpx_1    2752
vpy_1    2048
Name: 1441, dtype: int64
1442
vpx_1    2752
vpy_1    2048
Name: 1442, dtype: int64
1443
vpx_1    2752
vpy_1    1952
Name: 1443, dtype: int64
1444
vpx_1    2752
vpy_1    1952
Name: 1444, dtype: int64
1445
vpx_1    2752
vpy_1    1952
Name: 1445, dtype: int64
1446
vpx_1    2752
vpy_1    1952
Name: 1446, dtype: int64
1447
vpx_1    2752
vpy_1    1952
Name: 1447, dtype: int64
1448
vpx_1    2752
vpy_1    1952
Name: 1448, dtype: int64
1449
vpx_1    2752
vpy_1    1952
Name: 1449, dtype: int64
1450
vpx_1    2752
vpy_1    1952
Name: 1450, dtype: int64
1451
vpx_1    

Name: 1916, dtype: int64
1917
vpx_1    3424
vpy_1    3584
Name: 1917, dtype: int64
1918
vpx_1    3424
vpy_1    3584
Name: 1918, dtype: int64
1919
vpx_1    3424
vpy_1    3584
Name: 1919, dtype: int64
1920
vpx_1    3424
vpy_1    3584
Name: 1920, dtype: int64
1921
vpx_1    3424
vpy_1    3584
Name: 1921, dtype: int64
1922
vpx_1    3424
vpy_1    3584
Name: 1922, dtype: int64
1923
vpx_1    3424
vpy_1    3584
Name: 1923, dtype: int64
1924
vpx_1    3424
vpy_1    3584
Name: 1924, dtype: int64
1925
vpx_1    3424
vpy_1    3584
Name: 1925, dtype: int64
1926
vpx_1    3424
vpy_1    3584
Name: 1926, dtype: int64
1927
vpx_1    3424
vpy_1    3584
Name: 1927, dtype: int64
1928
vpx_1    3424
vpy_1    3584
Name: 1928, dtype: int64
1929
vpx_1    3424
vpy_1    3584
Name: 1929, dtype: int64
1930
vpx_1    3424
vpy_1    3584
Name: 1930, dtype: int64
1931
vpx_1    3424
vpy_1    3584
Name: 1931, dtype: int64
1932
vpx_1    3424
vpy_1    3584
Name: 1932, dtype: int64
1933
vpx_1    3424
vpy_1    3584
Name: 1933, dt

...

Name: 26208, dtype: int64
26209
vpx_1    2784
vpy_1    1792
Name: 26209, dtype: int64
26210
vpx_1    2784
vpy_1    1792
Name: 26210, dtype: int64
26211
vpx_1    2784
vpy_1    1792
Name: 26211, dtype: int64
26212
vpx_1    2784
vpy_1    1792
Name: 26212, dtype: int64
26213
vpx_1    2784
vpy_1    1792
Name: 26213, dtype: int64
26214
vpx_1    2784
vpy_1    1792
Name: 26214, dtype: int64
26215
vpx_1    2784
vpy_1    1792
Name: 26215, dtype: int64
26216
vpx_1    2784
vpy_1    1792
Name: 26216, dtype: int64
26217
vpx_1    2784
vpy_1    1792
Name: 26217, dtype: int64
26218
vpx_1    2784
vpy_1    1792
Name: 26218, dtype: int64
26219
vpx_1    2784
vpy_1    1792
Name: 26219, dtype: int64
26220
vpx_1    2784
vpy_1    1792
Name: 26220, dtype: int64
26221
vpx_1    2784
vpy_1    1792
Name: 26221, dtype: int64
26222
vpx_1    2784
vpy_1    1792
Name: 26222, dtype: int64
26223
vpx_1    2784
vpy_1    1792
Name: 26223, dtype: int64
26224
vpx_1    2784
vpy_1    1792
Name: 26224, dtype: int64
26225
vpx_1   

Name: 26695, dtype: int64
26696
vpx_1     288
vpy_1    3104
Name: 26696, dtype: int64
26697
vpx_1     288
vpy_1    3104
Name: 26697, dtype: int64
26698
vpx_1     288
vpy_1    3104
Name: 26698, dtype: int64
26699
vpx_1     288
vpy_1    3104
Name: 26699, dtype: int64
26700
vpx_1     288
vpy_1    3104
Name: 26700, dtype: int64
26701
vpx_1     288
vpy_1    3104
Name: 26701, dtype: int64
26702
vpx_1     288
vpy_1    3104
Name: 26702, dtype: int64
26703
vpx_1     288
vpy_1    3104
Name: 26703, dtype: int64
26704
vpx_1     288
vpy_1    3104
Name: 26704, dtype: int64
26705
vpx_1     576
vpy_1    3168
Name: 26705, dtype: int64
26706
vpx_1     576
vpy_1    3168
Name: 26706, dtype: int64
26707
vpx_1     576
vpy_1    3168
Name: 26707, dtype: int64
26708
vpx_1     576
vpy_1    3168
Name: 26708, dtype: int64
26709
vpx_1     576
vpy_1    3168
Name: 26709, dtype: int64
26710
vpx_1     576
vpy_1    3168
Name: 26710, dtype: int64
26711
vpx_1     576
vpy_1    3168
Name: 26711, dtype: int64
26712
vpx_1   

27170
vpx_1    2592
vpy_1    2688
Name: 27170, dtype: int64
27171
vpx_1    2592
vpy_1    2688
Name: 27171, dtype: int64
27172
vpx_1    2592
vpy_1    2688
Name: 27172, dtype: int64
27173
vpx_1    2592
vpy_1    2688
Name: 27173, dtype: int64
27174
vpx_1    2592
vpy_1    2688
Name: 27174, dtype: int64
27175
vpx_1    2592
vpy_1    2688
Name: 27175, dtype: int64
27176
vpx_1    2592
vpy_1    2688
Name: 27176, dtype: int64
27177
vpx_1    2592
vpy_1    2688
Name: 27177, dtype: int64
27178
vpx_1    2592
vpy_1    2688
Name: 27178, dtype: int64
27179
vpx_1    2592
vpy_1    2688
Name: 27179, dtype: int64
27180
vpx_1    2592
vpy_1    2688
Name: 27180, dtype: int64
27181
vpx_1    2592
vpy_1    2688
Name: 27181, dtype: int64
27182
vpx_1    2592
vpy_1    2688
Name: 27182, dtype: int64
27183
vpx_1    2592
vpy_1    2688
Name: 27183, dtype: int64
27184
vpx_1    2592
vpy_1    2688
Name: 27184, dtype: int64
27185
vpx_1    2592
vpy_1    2688
Name: 27185, dtype: int64
27186
vpx_1    2592
vpy_1    2688
Name: 

Name: 27627, dtype: int64
27628
vpx_1    2720
vpy_1    2528
Name: 27628, dtype: int64
27629
vpx_1    2720
vpy_1    2560
Name: 27629, dtype: int64
27630
vpx_1    2720
vpy_1    2560
Name: 27630, dtype: int64
27631
vpx_1    2720
vpy_1    2560
Name: 27631, dtype: int64
27632
vpx_1    2720
vpy_1    2560
Name: 27632, dtype: int64
27633
vpx_1    2720
vpy_1    2560
Name: 27633, dtype: int64
27634
vpx_1    2720
vpy_1    2560
Name: 27634, dtype: int64
27635
vpx_1    2720
vpy_1    2560
Name: 27635, dtype: int64
27636
vpx_1    2720
vpy_1    2560
Name: 27636, dtype: int64
27637
vpx_1    2720
vpy_1    2560
Name: 27637, dtype: int64
27638
vpx_1    2720
vpy_1    2560
Name: 27638, dtype: int64
27639
vpx_1    2720
vpy_1    2560
Name: 27639, dtype: int64
27640
vpx_1    2720
vpy_1    2560
Name: 27640, dtype: int64
27641
vpx_1    2720
vpy_1    2560
Name: 27641, dtype: int64
27642
vpx_1    2720
vpy_1    2560
Name: 27642, dtype: int64
27643
vpx_1    2592
vpy_1    2560
Name: 27643, dtype: int64
27644
vpx_1   

Name: 28091, dtype: int64
28092
vpx_1    2528
vpy_1    2528
Name: 28092, dtype: int64
28093
vpx_1    2528
vpy_1    2528
Name: 28093, dtype: int64
28094
vpx_1    2528
vpy_1    2528
Name: 28094, dtype: int64
28095
vpx_1    2528
vpy_1    2528
Name: 28095, dtype: int64
28096
vpx_1    2528
vpy_1    2528
Name: 28096, dtype: int64
28097
vpx_1    2528
vpy_1    2528
Name: 28097, dtype: int64
28098
vpx_1    2528
vpy_1    2528
Name: 28098, dtype: int64
28099
vpx_1    2528
vpy_1    2528
Name: 28099, dtype: int64
28100
vpx_1    2528
vpy_1    2528
Name: 28100, dtype: int64
28101
vpx_1    2528
vpy_1    2528
Name: 28101, dtype: int64
28102
vpx_1    2688
vpy_1    2240
Name: 28102, dtype: int64
28103
vpx_1    2688
vpy_1    2240
Name: 28103, dtype: int64
28104
vpx_1    2688
vpy_1    2240
Name: 28104, dtype: int64
28105
vpx_1    2688
vpy_1    2240
Name: 28105, dtype: int64
28106
vpx_1    2688
vpy_1    2240
Name: 28106, dtype: int64
28107
vpx_1    2688
vpy_1    2240
Name: 28107, dtype: int64
28108
vpx_1   

In [137]:
channel_vpds

array([[[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 5., ..., 0., 0., 0.],
        [0., 0., 5., ..., 0., 0., 0.],
        [0., 0., 5., ..., 0., 0., 0.]],

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 5., ..., 0., 0., 0.],
        [0., 0., 5., ..., 0., 0., 0.],
        [0., 0., 5., ..., 0., 0., 0.]],

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 5., ..., 0., 0., 0.],
        [0., 0., 5., ..., 0., 0., 0.],
        [0., 0., 5., ..., 0., 0., 0.]],

       ...,

       [[0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        ...,
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0., 0.],
        [0., 0., 0., ..., 0., 0.

In [91]:
kernel.shape

(20, 12)

In [99]:
frames.shape

(28253, 128, 128)

In [101]:
frames[0][10:10+20,10:10+12].shape

(20, 12)

In [103]:
frames[0][10:10+20,10:10+12] += kernel

In [105]:
frames[0][10:10+20,10:10+12]

array([[1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.],
       [1., 1., 1., 1., 1., 1.,

In [87]:
frames.shape

(28253, 128, 128)

In [85]:
ORIGIN_SHAPE

(128, 128)

In [78]:
dataframe123

vpx_1  vpy_1
frame              
0       3424     64
1       3424     64
2       3424     64
3       3424     64
4       3424     64
...      ...    ...
28248   2752   2624
28249   2752   2656
28250   2752   2656
28251   2752   2656
28252   2752   2656

[28253 rows x 2 columns]

In [82]:
channel_vpd_label = mapping_vpd_into_channel(dataframe123, num_dataset=2)

ValueError: operands could not be broadcast together with shapes (0,12) (20,12) (0,12) 

In [ ]:
# def mapping_vpd_into_channel(vpds_tile, kernel_shape=KERNEL_SHAPE, origin_shape=ORIGIN_SHAPE):

In [ ]:

frames = np.zeros((np.max(vpds_tile.index.max()) + 1,) + (origin_shape))
kernel = np.ones(kernel_shape)
    
#     for idx, row in vpds_tile.iterrows():
#         for i in range(num_dataset):
#             frames[idx][row['vpx_{}'.format(i+1)]:row['vpx_{}'.format(i+1)] + kernel.shape[0], row['vpy_{}'.format(i+1)]:row['vpy_{}'.format(i+1)] + kernel_shape[1]] += kernel
#     return frames     

In [62]:
vpds_tile

vpx_1  vpy_1  vpx_2  vpy_2  vpx_3  vpy_3  vpx_4  vpy_4  vpx_5  vpy_5
frame                                                                      
0        108      2    108      2    108      2    108      2    108      2
1        108      2    108      2    108      2    108      2    108      2
2        108      2    108      2    108      2    108      2    108      2
3        108      2    108      2    108      2    108      2    108      2
4        108      2    108      2    108      2    108      2    108      2
...      ...    ...    ...    ...    ...    ...    ...    ...    ...    ...
28248     79     79     83     82     86     85     86     81     86     83
28249     79     79     83     82     86     85     86     83     86     83
28250     79     79     83     82     86     85     86     83     86     83
28251     79     79     83     82     86     84     86     83     86     83
28252     79     79     83     82     86     84     86     83     86     83

[28253 rows x 10 columns]

In [68]:
channel_vpd_label = mapping_vpd_into_channel(dataframe123)

KeyError: 'vpx_1'

In [58]:
channel_vpds.shape

(28253, 128, 128)

In [61]:
channel_vpds[100]

array([[0., 3., 3., ..., 0., 0., 0.],
       [0., 3., 3., ..., 0., 0., 0.],
       [0., 3., 3., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.]])

In [55]:
max_vpd_coords/32

array([[107.,   2.],
       [107.,   2.],
       [107.,   2.],
       ...,
       [ 86.,  83.],
       [ 86.,  83.],
       [ 86.,  83.]])

In [56]:
max_vpd_coords.shape

(28253, 2)

In [57]:
result = np.zeros((width_tile, height_tile))

NameError: name 'width_tile' is not defined

In [41]:
vpds_tile['vpx_1'][0]

108

In [42]:
vpds_tile['vpy_1'][0]

2

In [43]:
k[127,2] = 1

In [44]:
k

array([[0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       ...,
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 0., ..., 0., 0., 0.],
       [0., 0., 1., ..., 0., 0., 0.]])

In [31]:
channel_vpds = mapping_vpd_into_channel(vpds_tile)

In [34]:
channel_kernel_sums, max_vpd_coords = vpds_tile_into_channel_kernel_sum(channel_vpds)

TypeError: 'module' object is not callable